In [24]:
from datetime import datetime

In [25]:
import pandas as pd
import sys
sys.path.append("../scripts/")
from extractor import DataExtractor

In [26]:
data_extractor=DataExtractor()

In [27]:
with open('../data/engagementmetrics.csv','r') as f:
    lines=f.readlines()

columns=lines[0].replace('\n','').split(';')
data=lines[1:]

In [28]:
df = pd.read_csv('../data/engagementmetrics.csv')

In [29]:
df.head()

Project ID                          EngagementID  \
0  108fb3bc-d8db-4c0c-987a-08f9cca99509  763613fe-8c2c-41e5-a0bc-7b724823303e   
1  264c17f0-f04d-431d-aed5-3f028b10619d  c0b65b93-61e3-44c8-b72e-93f521ccd72e   
2  cc84eca6-9a64-4131-b113-532aad2c3012  f7d55a89-5211-4e0f-ab51-c48d28a8d090   
3  0eb07af5-7f7f-4376-a0c4-62cadcfa8f8d  574994e2-3f90-410e-b7ec-0ba8ea50602a   
4  b6a7dab7-05f6-420a-9729-5231653f208f  6b18a7ea-fe19-4bb8-8985-93e7950e92c7   

   Customer ID Customer Name Engagement Date    Revenue   Revenue USD  \
0        799.0           NaN      24-08-2020   $1407730     $98548970   
1        821.0           NaN      18.09.2022      $9140        43955k   
2          NaN  Customer_675             NaN        NaN     $72029.28   
3        142.0  Customer_784      07/31/2017  $65383690  15623.54 USD   
4         81.0           NaN      30-12-2011     91614k  21317.49 USD   

       Service       Sub-Service Engagement Type Employee Count    Comments  \
0   Consulting           Backend        One-time            343  Comment 60   
1  Development  Customer Service       Recurring           1505  Comment 75   
2       Design          Frontend             New          fifty  Comment 45   
3  Development           Backend             Nqw            601  Comment 16   
4   Consulting          Frontend             New          fifty  Comment 58   

                            Project Ref Engagement Reference Client Revenue  \
0  c2b246b5-e65f-40f6-af21-706706b5e77b            ENG-04938       $51561.3   
1  a0bff16b-91ca-4fd1-b98e-59eba8a1eea1            ENG-07622       53426650   
2  7ef70aa7-a663-4c28-bb37-767858ac1695            ENG-06044         $20469   
3  c6f563e8-3c3f-46bd-9ea4-a4bc83aa85b9            ENG-08716      $66159.03   
4  b0b9c377-4b54-43c8-90b3-ba71d48a59fb            ENG-00405       71776540   

  Service Type Detailed Sub-Service  
0       Design     Cuswomer Service  
1      Support                UX/UI  
2      Support                UX/UI  
3   Consulting             Frontend  
4       Design     Customer Service

In [30]:
from ydata_profiling import ProfileReport
report = ProfileReport(df, title="Profiling Report")

In [31]:
report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [32]:
df['Customer ID'].unique()

array([799., 821.,  nan, ..., 193., 463., 507.])

Summary 

Project ID - Does not have null values
Engagement ID - Does not have null values
Customer ID - Does contain null values but all are type float
Customer Name - have different spellings of Customer and different ways of writing
Engagement Date - Has different date format that need to normalized


Checking all the fields

In [33]:
df['Customer ID'].dtypes

dtype('float64')

In [34]:
df['Customer ID'].dtypes

dtype('float64')

In [35]:

def normalize_date(date_str):
    """
    Normalize a date string to DD/MM/YYYY format.
    Handles MM/DD/YYYY, DD/MM/YYYY, and YYYY/MM/DD formats.
    """
    if pd.isnull(date_str):  # Check for null or NaN values
        return None
        
    for fmt in ("%m/%d/%Y", "%d/%m/%Y", "%Y/%m/%d"):
        try:
            # Try parsing the date with the current format
            parsed_date = datetime.strptime(date_str, fmt)
            # Return the date in DD/MM/YYYY format
            return parsed_date.strftime("%d/%m/%Y")
        except ValueError:
            continue
    # Return None if the date format is unrecognized
    return None

# replace other characters in Date
df['Engagement Date'] = df['Engagement Date'].str.replace(r"[.\-]", "/", regex=True)

# Apply normalization to the dataset
df["Engagement Date"] = df["Engagement Date"].apply(normalize_date)

# Show the results
#print(df)

Disregard the missing Customer ID and Customer Name - they seem to be okay as long as we have project ID which will link to the customer ID in the DIM table

In [36]:
filtered_df = df[df['Revenue'].isna()]
display(filtered_df)

#.str.contains("k")

Project ID  \
2      cc84eca6-9a64-4131-b113-532aad2c3012   
28     03d2b74e-1966-4361-947d-b89e2fd2e50c   
49     2b9ed833-c697-4ff1-a830-6515ea5a54b3   
102    923b2925-3a4e-4451-8f55-3181e5afa52c   
166    b86d2304-723a-4fdd-823d-32b106751625   
...                                     ...   
99915  810312b1-4504-47cf-880f-9339e49afb34   
99926  e40ba69f-5c4d-46d5-9ab4-dbcdb7eeeacf   
99936  95ea03db-9eab-4b5a-950f-1b2b43fd7805   
99944  bdd12477-f306-40b7-95f6-e63255b8f9a1   
99946  894e5e0c-6e71-42ef-b845-23e924135e4e   

                               EngagementID  Customer ID Customer Name  \
2      f7d55a89-5211-4e0f-ab51-c48d28a8d090          NaN  Customer_675   
28     d23dfa0b-25e5-4a48-b523-d61b432bd438        828.0  Customer_721   
49     a58f3053-78f3-421d-aab0-61a2ca656d3b        482.0  Customer_148   
102    033e1836-59c5-45da-9deb-d1bf8991e2e1        739.0  Customer_286   
166    4a048234-3500-4668-b116-3ac0c2adee8b        504.0           NaN   
...                                     ...          ...           ...   
99915  68f70d90-3971-422c-af9f-3d6eeaa55482        729.0  CUSTOMER_467   
99926  6cfdddb7-7a47-44f9-82ce-98ae9ca6e705        613.0  Customer_291   
99936  1cfc95ec-c457-45e0-b8f5-05292bd92631        272.0  Customer_184   
99944  4db9ef7a-3a04-4e63-9b05-b1f0ee6906de        308.0  Customer_5n6   
99946  7088d1ed-3811-4c2d-8aa4-2f6835d28f31        285.0  Customer_188   

      Engagement Date Revenue   Revenue USD      Service       Sub-Service  \
2                None     NaN     $72029.28       Design          Frontend   
28         30/05/2014     NaN      96505310       Design             UX/UI   
49         26/07/2021     NaN  22449.45 USD   Consulting  Customer Service   
102        29/01/2020     NaN   10050.6 USD      Support          Strategy   
166        01/10/2011     NaN  29675.59 USD   Consulting          Strategy   
...               ...     ...           ...          ...               ...   
99915      26/01/2018     NaN     $61784920       Design           Bzckend   
99926      13/11/2023     NaN      $6888090  Development             UX/UI   
99936      22/02/2020     NaN     $27348920       Design           Backend   
99944      26/08/2012     NaN     $60186410   Consulting          Strategy   
99946      17/05/2010     NaN      97094.05  Development          Frontend   

      Engagement Type Employee Count     Comments  \
2                 New          fifty   Comment 45   
28           One-time          fifty          NaN   
49          Recurring            788   Comment 99   
102         Recurring        hundred   Comment 40   
166         Recurring             61          NaN   
...               ...            ...          ...   
99915        One-time           2442   Comment 50   
99926        One-time            NaN    Comment 3   
99936        One-time        hundred   Comment 19   
99944             New            658  Comment 100   
99946        One-time        hundred    Comment 5   

                                Project Ref Engagement Reference  \
2      7ef70aa7-a663-4c28-bb37-767858ac1695            ENG-06044   
28     ddf2a22e-c15d-44e7-95b9-451e98475cb7            ENG-09911   
49     70c51a44-4e0f-4681-b080-f165a1bbace8            ENG-03194   
102    7f6952b2-63fa-48ea-a78a-b0d56fdd11dc            ENG-01116   
166    47bdae1b-8fcf-491d-b91a-97f508425eed            ENG-03737   
...                                     ...                  ...   
99915  dfa9c4bb-5c1d-490b-b8c3-5279da690fdc            ENG-00785   
99926  24aa403c-85f9-465c-8a8a-2b8555cb09bf            ENG-03500   
99936  3a50e607-d867-4627-9d45-e121203d76f3            ENG-08450   
99944  084cb558-ae71-42ef-b9de-ed6c1ce89ec1            ENG-08614   
99946  8b121f9c-7266-4531-8be4-ba5c7026c811            ENG-05782   

      Client Revenue Service Type Detailed Sub-Service  
2             $20469      Support                UX/UI  
28         $74023.27       Design             Frontend  
49      55815.13 

In [37]:
filtered_df = df[df['Project ID'] == '069a308a-691c-4236-9e8a-ab6422d1ed65']
display(filtered_df)

Project ID  \
212    069a308a-691c-4236-9e8a-ab6422d1ed65   
25212  069a308a-691c-4236-9e8a-ab6422d1ed65   
50212  069a308a-691c-4236-9e8a-ab6422d1ed65   
75212  069a308a-691c-4236-9e8a-ab6422d1ed65   

                               EngagementID  Customer ID Customer Name  \
212    f783318d-f0c4-440f-9ac9-cee80bf4ac3a          NaN           NaN   
25212  07347c52-dc50-499a-bc87-b694a09c5d84        789.0  Customer_649   
50212  3c00b5ad-3d0f-45c0-999e-40954ab9046d          2.0  Customer_754   
75212  8723cbc8-8868-4afe-a074-b7422062b2be         87.0  Customer_219   

      Engagement Date    Revenue   Revenue USD      Service       Sub-Service  \
212        04/08/2024  $15246570        $69910  Development           Backend   
25212      06/11/2014    9064040     $89604.67   Consulting             rX/UI   
50212      19/02/2020     $17210      55020700      Support  Customer Service   
75212      25/03/2013   46196570  97135.44 USD       Design          Strategy   

      Engagement Type Employee Count    Comments  \
212          One-time            167  Comment 93   
25212        One-time             13  Comment 14   
50212             New           2696  Comment 58   
75212        One-time        hundred  Comment 63   

                                Project Ref Engagement Reference  \
212    76f1ed79-68c0-47b9-a759-bdf4d9804753            ENG-00521   
25212  9768db83-3262-4964-82d9-6fa21d63d450            ENG-06348   
50212  019ac2d6-92a4-4da8-bd5a-8fac3b429198            ENG-02243   
75212  24beea8d-e725-44bf-8780-924907421f99            ENG-09418   

      Client Revenue Service Type Detailed Sub-Service  
212     58110.67 USD   Consulting             Strategy  
25212          $1568  Development             Strategy  
50212       19009.55  Development                UX/UI  
75212       $4130000  Development             Strategy

In [38]:
def load_public_google_sheet_to_dataframe(sheet_url: str) -> pd.DataFrame:
    """
    Load data from a public Google Spreadsheet into a Pandas DataFrame.

    Args:
        sheet_url (str): URL of the Google Spreadsheet.

    Returns:
        pd.DataFrame: Data loaded into a DataFrame.
    """
    # Convert the Google Sheets URL to its CSV export format
    csv_export_url = sheet_url.replace('/edit?gid=', '/export?format=csv&gid=')

    # Load the data into a DataFrame
    try:
        df = pd.read_csv(csv_export_url)
        return df
    except Exception as e:
        raise ValueError(f"Error loading data from the Google Sheet: {e}")

# Example usage:
sheet_url = "https://docs.google.com/spreadsheets/d/1-WIUFMWoAiNIMyVyNj4KKlk4Mrxkg0sIRdjarRqtrVs/edit?gid=666332733"
df = load_public_google_sheet_to_dataframe(sheet_url)
df

Project ID  \
0      108fb3bc-d8db-4c0c-987a-08f9cca99509   
1      264c17f0-f04d-431d-aed5-3f028b10619d   
2      cc84eca6-9a64-4131-b113-532aad2c3012   
3      0eb07af5-7f7f-4376-a0c4-62cadcfa8f8d   
4      b6a7dab7-05f6-420a-9729-5231653f208f   
...                                     ...   
99995  aad217eb-2ced-49a5-abaa-da70e862f89d   
99996  e5e8f42d-8761-4220-b299-e2bc13d3721f   
99997  1812e551-768a-4d13-a9df-4be12065c658   
99998  eced7aa4-0443-45f2-b4c6-815963c2d58b   
99999  ede4b0fb-8cba-4f79-bba3-f11dd062e5c0   

                               EngagementID  Customer ID Customer Name  \
0      763613fe-8c2c-41e5-a0bc-7b724823303e        799.0           NaN   
1      c0b65b93-61e3-44c8-b72e-93f521ccd72e        821.0           NaN   
2      f7d55a89-5211-4e0f-ab51-c48d28a8d090          NaN  Customer_675   
3      574994e2-3f90-410e-b7ec-0ba8ea50602a        142.0  Customer_784   
4      6b18a7ea-fe19-4bb8-8985-93e7950e92c7         81.0           NaN   
...                                     ...          ...           ...   
99995  61633bdd-fd62-4517-b706-d46e1a208e23        474.0  Customer_610   
99996  80871e47-85f7-446f-93cd-b6c06779759b        119.0  Customer_233   
99997  97831fb4-49d2-4201-b04e-da420facf053         97.0  Customer_474   
99998  5edcb88c-28d3-4fed-8184-9e8a3dceb87c        666.0  Customer_670   
99999  2b419e4f-eab5-4ecb-98be-3c61a7cbd452          NaN  Customer_307   

      Engagement Date       Revenue   Revenue USD      Service  \
0          24-08-2020      $1407730     $98548970   Consulting   
1          18.09.2022         $9140        43955k  Development   
2                 NaN           NaN     $72029.28       Design   
3          07/31/2017     $65383690  15623.54 USD  Development   
4          30-12-2011        91614k  21317.49 USD   Consulting   
...               ...           ...           ...          ...   
99995      05/22/2011      47109600       9471070      Support   
99996      11.09.2018  26533.83 USD     $48437030  Development   
99997             NaN     $10062400     $12299.39      iupport   
99998      03/10/2018        $13758   29153.7 USD      Support   
99999      31-07-2024  54923.01 USD        $93059   Consulting   

            Sub-Service Engagement Type Employee Count    Comments  \
0               Backend        One-time            343  Comment 60   
1      Customer Service       Recurring           1505  Comment 75   
2              Frontend             New          fifty  Comment 45   
3               Backend             Nqw            601  Comment 16   
4              Frontend             New          fifty  Comment 58   
...                 ...             ...            ...         ...   
99995             UX/UI        One-time           2429  Comment 50   
99996             eX/UI       Recurring            NaN  Comment 66   
99997             UX/UI       Recurring            NaN  Comment 57   
99998          Frontend        One-time        hundred  Comment 50   
99999  Customer Service        One-time        hundred  Comment 21   

                                Project Ref Engagement Reference  \
0      c2b246b5-e65f-40f6-af21-706706b5e77b            ENG-04938   
1      a0bff16b-91ca-4fd1-b98e-59eba8a1eea1            ENG-07622   
2      7ef70aa7-a663-4c28-bb37-767858ac1695            ENG-06044   
3      c6f563e8-3c3f-46bd-9ea4-a4bc83aa85b9            ENG-08716   
4      b0b9c377-4b54-43c8-90b3-ba71d48a59fb            ENG-00405   
...                                     ...                  ...   
99995  7f029713-6bc5-43ac-826b-73faaa610660            ENG-08956   
99996  0e9e1fa6-cce9-4af0-b910-2cc19c702b72                  NaN   
99997  f8abd7a6-fa6d-4b35-9c71-e66cab820514            ENG-05690   
99998  7c06642d-a624-444f-95a5-f61df54591e1            ENG-08739   
99999  ef0dfea5-d27b-4a3e-b46b-045a107912bb            ENG-02991   

      Client Revenue Service Type Detailed Sub-Service  
0           $51561.3       Design     Cuswomer Service  
1           53

In [70]:
# Columns to check the words: Service, Sub-Service, Engagement Type, Service Type, Detailed Sub-Service
len(df['Employee Count'].value_counts())

4883

In [41]:
from rapidfuzz import process

In [64]:
# Correct words list
correct_words = ["Design", "Support", "Consulting", "Development", "Backend", "Frontend" , "UX/UI", "Customer Service", "Strategy", "Recurring", "New", "One-time"]

# Match misspelled words to correct words
data = {
    "word": misspelled_words,
    "correct_word": [process.extractOne(word, correct_words)[0] for word in misspelled_words],
    "update_date": [pd.Timestamp.now().strftime("%Y-%m-%d")] * len(misspelled_words),
}

# Create DataFrame
word_df= pd.DataFrame(data)
print(word_df)

          word      correct_word update_date
0        Desgn            Design  2024-12-09
1       supprt           Support  2024-12-09
2    conslting        Consulting  2024-12-09
3    devlopmnt       Development  2024-12-09
4      Szpport           Support  2024-12-09
5       Desiwn            Design  2024-12-09
6        UX/zI             UX/UI  2024-12-09
7   zonsulting        Consulting  2024-12-09
8   Cosmr srvc  Customer Service  2024-12-09
9       oesign            Design  2024-12-09
10         Nej               New  2024-12-09
11         uew               New  2024-12-09
12      1-time          One-time  2024-12-09
13         1-x          One-time  2024-12-09


In [67]:
# Function to map misspelled words to correct words
def map_correct_word(column, correct_words):
    return column.apply(lambda x: process.extractOne(x, correct_words)[0] if pd.notnull(x) else x)


def word_mapping():
    # Correct words list
    correct_words = ["Design", "Support", "Consulting", "Development", "Backend", "Frontend" , "UX/UI", "Customer Service", "Strategy", "Recurring", "New", "One-time"]
    
    # Create a list to store mappings
    mappings = []
    
    # Iterate through each column that needs processing
    for col in ["Service", "Sub-Service", "Engagement Type", "Service Type", "Detailed Sub-Service"]:
        # Apply the mapping function
        df[col + "_Corrected"] = map_correct_word(df[col], correct_words)
        
        # Append mappings to the list for building the output DataFrame
        column_mappings = pd.DataFrame({
            "word": df[col],
            "correct_word": df[col + "_Corrected"],
            "update_date": pd.Timestamp.now().strftime("%Y-%m-%d")
        })
        mappings.append(column_mappings)
    
    # Combine all mappings into a single DataFrame
    final_mappings = pd.concat(mappings).drop_duplicates().reset_index(drop=True)

# Display the final mappings DataFrame
print(final_mappings)

                  word      correct_word update_date
0           Consulting        Consulting  2024-12-09
1          Development       Development  2024-12-09
2               Design            Design  2024-12-09
3              Support           Support  2024-12-09
4          Davelopment       Development  2024-12-09
...                ...               ...         ...
2476  Customer xervice  Customer Service  2024-12-09
2477  Customer Servicb  Customer Service  2024-12-09
2478  Cuitomer Service  Customer Service  2024-12-09
2479  Cujtomer Service  Customer Service  2024-12-09
2480  Customer Sdrvice  Customer Service  2024-12-09

[2481 rows x 3 columns]


In [68]:
final_mappings.head(50)

word correct_word update_date
0    Consulting   Consulting  2024-12-09
1   Development  Development  2024-12-09
2        Design       Design  2024-12-09
3       Support      Support  2024-12-09
4   Davelopment  Development  2024-12-09
5    Cgnsulting   Consulting  2024-12-09
6    Consultinl   Consulting  2024-12-09
7    Conkulting   Consulting  2024-12-09
8   Developmeat  Development  2024-12-09
9    Consultikg   Consulting  2024-12-09
10   Consultinh   Consulting  2024-12-09
11  Develobment  Development  2024-12-09
12      Supzort      Support  2024-12-09
13   Consultrng   Consulting  2024-12-09
14   Consclting   Consulting  2024-12-09
15      Supporl      Support  2024-12-09
16   Consucting   Consulting  2024-12-09
17       tesign       Design  2024-12-09
18  Developmewt  Development  2024-12-09
19  Deveyopment  Development  2024-12-09
20      Szpport      Support  2024-12-09
21   Consllting   Consulting  2024-12-09
22       Desigx       Design  2024-12-09
23  Develovment  Development  2024-12-09
24      Supporj      Support  2024-12-09
25      Sgpport      Support  2024-12-09
26      Suppolt      Support  2024-12-09
27      Subport      Support  2024-12-09
28      Sdpport      Support  2024-12-09
29  Develojment  Development  2024-12-09
30      bupport      Support  2024-12-09
31   wonsulting   Consulting  2024-12-09
32       besign       Design  2024-12-09
33      Supporg      Support  2024-12-09
34       Desigo       Design  2024-12-09
35  Developwent  Development  2024-12-09
36   Consklting   Consulting  2024-12-09
37  Devblopment  Development  2024-12-09
38       Deyign       Design  2024-12-09
39   Consultung   Consulting  2024-12-09
40   Consuljing   Consulting  2024-12-09
41       Dtsign       Design  2024-12-09
42       Deszgn       Design  2024-12-09
43      Suzport      Support  2024-12-09
44  Developmeno  Development  2024-12-09
45       Dedign       Design  2024-12-09
46       Drsign       Design  2024-12-09
47       Dcsign       Design  2024-12-09
48  Developmedt  Development  2024-12-09
49       Dewign       Design  2024-12-09